# Week V - Duck Typing, Monte-Carlo & Block Averages, NumExpr

## Duck Typing

> If it walks like a duck and it quacks like a duck, then it must be a duck.

Often, we do not really care about the type of an object but we are interested only in its behaviour. In particular, we typically need to know whether certain methods are implemented.

**Duck typing** is a form of polymorphims where functions operate on any object that implements the appropiate methods, regardless of their classes or explicit interface declarations (L. Ramalho, *Fluent Python*, O'Reilly, 2016).

Let us do some tests:

In [ ]:
import numpy as np
def check_iterable(x):
    try:
        iter(x)
        print('{} is iterable'.format(x))
        return True
    except TypeError as err:
        print(err)
        return False
for x in [np.array([1,2,3]),[1,2,3],(1,2,3),'abcd',2]:
    check_iterable(x)
    

### Generators and the iterator protocol

In Python, there is a consistent way to iterate over sequences, no matter the specific object type. This happens thanks to an **iterator protocol**, which is a generic way to make objects iterable.
**Generators** allow to construct iterable objects, in a rather concise manner.


In [ ]:
range(10)

In [ ]:
np.arange(10)

In [ ]:
list(range(10))

In [ ]:
def gen_cube(N):
    for i in range(N):
        yield (i+1)**3
gen_cube(8)

In [ ]:
gen = gen_cube(8)

In [ ]:
for i in gen:
    print(i)

------------------------------

## Exercise - Block Averages and Monte-Carlo 

>Let's write a code that calculates $\pi$ with Monte-Carlo sampling and block averages.

We will employ a uniform random distribution $x \in [0,1]$ to calculate $\pi$ with the following integral:

$$ 4\int_0^1 \sqrt{1-x^2} dx$$

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import numexpr as ne

class Integral:
    '''
    This class calculates \pi 
    through Monte Carlo integration
    '''
    
    def __init__(self,N,numexp=False):
        'Initialise the MC.'
        self.N = N
        self.rng = np.random.default_rng(seed=42424)
        self.I = 0.0
        self.I2 = 0.0
        self.stdvn = 0.0
        self.do_block_averages = None
        self.blocks = None
        self.var = None
        self.numexp = numexp
        
    def f(self,x):
        'Function to integrate.'
        return 4.0*np.sqrt(1.0-x**2)
    
    def f2(self,x):
        'Square of self.f, computationally faster.'
        return 16.0*(1.0-x**2)
    
    def compute_mc_integral(self,x):
        'Sample self.f and average.'
        if self.numexp:
           ev = ne.evaluate("(4.0*sqrt(1.0-x**2))",optimization='moderate')
           return np.average(ev)
        else:
            return sum(map(self.f, x))/len(x)

    def compute_mc_integral_var(self,x):
        '''
        Sample self.f and calculates
        mean, mean of the square, variance,
        standard deviation
        '''
        I = self.compute_mc_integral(x)
        I2 = sum(map(self.f2, x))/len(x)
        var = (I2 - I**2)
        stdvn =  np.sqrt((I2 - I**2)/len(x))
        return np.array([I,I2,stdvn,var])
        
    def mc_integral(self,block_averages=False,blocks=1):
        'MC integration driver'
        self.do_block_averages = block_averages
        self.blocks = blocks
        r = self.rng.random(self.N)
        if self.do_block_averages and self.blocks!=self.N:
            rs = np.split(r,self.blocks)
            results = np.array(list(map(self.compute_mc_integral,rs)))
            self.I = np.average(results)
            self.I2 =  np.average(results**2)
            self.stdvn = np.sqrt((self.I2 - self.I**2)/results.shape[0])
            self.var = (self.I2 - self.I**2)
        else:
            self.I,self.I2,self.stdvn,self.var = self.compute_mc_integral_var(r)


In [ ]:
integral = Integral(10000)
integral.mc_integral()
for i in range(5):
    integral.mc_integral()
    print(integral.I)

In [ ]:
y = []
yy = []
x = range(100,200000,1000)
for N in x:
    integral = Integral(N)
    integral.mc_integral()
    y.append(integral.I)
    yy.append(abs(integral.I - np.pi))

In [ ]:
plt.plot(x,y,'o-')
plt.axhline(np.pi,c='k',alpha=0.5)

Now we check whether the true error goes down as $1/\sqrt{N}$.

In [ ]:
plt.loglog(x,yy,'o-')
plt.loglog(x,list(map(lambda x: 1/np.sqrt(x),x)))

In [ ]:
# Whole data set
N=10000
integral = Integral(N)
integral.mc_integral()
print('I = {:.5f}, variance = {:.5f}, stdvn = {:.5f}, Delta= {:.5f}'.
      format(integral.I,integral.var, integral.stdvn, abs(integral.I-np.pi)))
print('-'*20)
print('sigma_n = {}'.format(integral.stdvn*np.sqrt(N)))
print('sigma_n/sqrt(N) = {}'.format(integral.stdvn))

In [ ]:
#Bloch averages: method 1
N = int(1e4)
l_I = []
l_I2 = []
integral = Integral(N)
NN = 10
for i in range(NN):
    integral.mc_integral()
    print('I = {:.5f}, variance = {:.5f}, stdvn = {:.5f}, Delta= {:.5f}'.format(integral.I,integral.var, 
                                                                integral.stdvn, abs(integral.I-np.pi)))
    l_I.append(integral.I)
    l_I2.append(integral.I**2)
var = np.average(l_I2)-(np.average(l_I))**2
sigma_m = np.sqrt(var)
print('-'*20)
print('sigma_m = {:.5f}'.format(sigma_m))

In [ ]:
#Bloch averages: method 2
N=10000
integral = Integral(N)
integral.mc_integral(block_averages=True,blocks=10)
print('I = {:.5f}, variance = {:.5f}, stdvn = {:.5f}, Delta= {:.5f}'.\
      format(integral.I,integral.var, integral.stdvn, abs(integral.I-np.pi)))
print('-'*20)
print('sigma_s/sqrt(s) = {:.5f}'.format(integral.stdvn))

-------------

# NumExpr

In [ ]:
%load_ext line_profiler
integral = Integral(int(1e6))
%lprun -f Integral.mc_integral integral.mc_integral(block_averages=True,blocks=100)

In [ ]:
%lprun -f Integral.compute_mc_integral integral.mc_integral(block_averages=True,blocks=100)

In [ ]:
integral = Integral(int(1e6),numexp=False)
%timeit integral.mc_integral(block_averages=True,blocks=10)
print(integral.I,integral.stdvn)
integral = Integral(int(1e6),numexp=True)
%timeit integral.mc_integral(block_averages=True,blocks=10)
print(integral.I,integral.stdvn)

In [ ]:
integral = Integral(int(1e6),numexp=True)
%lprun -f Integral.compute_mc_integral integral.mc_integral(block_averages=True,blocks=100)

> The ``NumExpr`` package provides tools for fast evaluation of array expressions. 
> It is particularly useful for **large arrays**.

The key to NumExpr’s speed is handling chunks of elements at a time. Default is 4096 elements at a time, using a register machine. NumExpr "sort of" compiles the expression in a vectorized manner and also support multi-threading parallelization by default. Check out the docs at: https://numexpr.readthedocs.io/en/latest/index.html
